In [0]:
from pyspark.sql import functions as F
from pyspark.sql.window import Window
import pandas
from pyspark.sql.functions import col
data_BASE_DIR = "dbfs:/mnt/mids-w261/"
display(dbutils.fs.ls(f"{data_BASE_DIR}"))
# Airline Data    
df_flights = spark.read.parquet(f"dbfs:/mnt/mids-w261/datasets_final_project_2022/parquet_airlines_data_1y/")
# Weather data
df_weather1 = spark.read.parquet(f"dbfs:/mnt/mids-w261/datasets_final_project_2022/parquet_weather_data_1y/")
# Stations data      
df_stations = spark.read.parquet(f"dbfs:/mnt/mids-w261/datasets_final_project_2022/stations_data/stations_with_neighbors.parquet/")
# OTPW
df_otpw = spark.read.format("csv").option("header","true").load(f"dbfs:/mnt/mids-w261/OTPW_12M/OTPW_12M/")
# Read in airport codes and timezones, drop columns to those two, filter out rows with no codes

df_airport_timezones = (spark.read
        .option("header", True)
        .option("inferSchema", True)
        .csv("dbfs:/FileStore/Group_4_3/Data/airports_codes_timezones_with_header.csv")
        .drop("airport_id", "name", "city", "country", "icao_code", "latitude", "longitude", "altitude", "dst", "tz_db_timezone", "type", "source") # drop everything but iata code and timezone
        .filter(F.col("iata_code") != "\\N") #filter out airports with no iata code
)

# Extensive feature engineering pipeline for flight turn metrics
#  - Computes time between previous arrival and scheduled departure
#  - Computes previous departure delay and previous arrival delay for the most recent preceding flight
#  - Enforces a minimum 2-hour turn threshold for joins


# ----------------------------------------------------------------------------
# STEP 1: Enrich original flights with local timezones for ORIGIN and DEST
# ----------------------------------------------------------------------------
# df_flights: base DataFrame of flights
# df_airport_timezones: mapping iata_code -> numeric timezone offset hours

df_enriched = (
    df_otpw.alias("fl")
      # ORIGIN timezone
      .join(
          df_airport_timezones
            .select(
              F.col("iata_code").alias("origin_iata"),
              F.col("timezone").alias("ORIGIN_TIMEZONE")
            ),
          on=F.col("fl.ORIGIN") == F.col("origin_iata"), how="left"
      ).drop("origin_iata")
      # DEST timezone
      .join(
          df_airport_timezones
            .select(
              F.col("iata_code").alias("dest_iata"),
              F.col("timezone").alias("DEST_TIMEZONE")
            ),
          on=F.col("fl.DEST") == F.col("dest_iata"), how="left"
      ).drop("dest_iata")
)

# ----------------------------------------------------------------------------
# STEP 2: Parse HHMM time fields to minutes since midnight
# ----------------------------------------------------------------------------
df_parsed = (
    df_enriched
      .withColumn("CRS_DEP_TIME_STR", F.lpad(F.col("CRS_DEP_TIME").cast("string"), 4, "0"))
      .withColumn("CRS_DEP_TIME_MINUTES",
          F.substring("CRS_DEP_TIME_STR", 1, 2).cast("int") * 60 +
          F.substring("CRS_DEP_TIME_STR", 3, 2).cast("int")
      )
      .withColumn("ARR_TIME_STR", F.lpad(F.col("ARR_TIME").cast("string"), 4, "0"))
      .withColumn("ARR_TIME_MINUTES",
          F.substring("ARR_TIME_STR", 1, 2).cast("int") * 60 +
          F.substring("ARR_TIME_STR", 3, 2).cast("int")
      )
      .withColumn("DEP_TIME_STR", F.lpad(F.col("DEP_TIME").cast("string"), 4, "0"))
      .withColumn("DEP_TIME_MINUTES",
          F.substring("DEP_TIME_STR", 1, 2).cast("int") * 60 +
          F.substring("DEP_TIME_STR", 3, 2).cast("int")
      )
)

# ----------------------------------------------------------------------------
# STEP 3: Build 'destination' DataFrame carrying previous delays & times
# ----------------------------------------------------------------------------
df_dest = df_parsed.select(
    F.col("TAIL_NUM").alias("dest_TAIL_NUM"),
    F.col("DEST").alias("dest_AIRPORT"),
    F.col("FL_DATE").alias("dest_FL_DATE"),
    F.col("ARR_DELAY").alias("PREV_ARR_DELAY"),
    F.col("ARR_TIME_MINUTES").alias("prev_ARR_TIME_MINUTES"),
    F.col("DEP_DELAY").alias("prev_DEP_DELAY"),
    F.col("DEP_TIME_MINUTES").alias("prev_DEP_TIME_MINUTES")
)

# ----------------------------------------------------------------------------
# STEP 4: Join to potential preceding flights by tail & origin
# ----------------------------------------------------------------------------
df_joined = df_parsed.alias("orig").join(
    df_dest,
    on=(
        (F.col("orig.TAIL_NUM") == F.col("dest_TAIL_NUM")) &
        (F.col("orig.ORIGIN") == F.col("dest_AIRPORT")) &
        (
            (F.col("orig.FL_DATE") == F.col("dest_FL_DATE")) |
            (F.col("orig.FL_DATE") == F.date_add(F.col("dest_FL_DATE"), 1))
        )
    ), how="left"
)

# ----------------------------------------------------------------------------
# STEP 5: Pre-compute adjusted arrival minutes for window tie-breaker
# ----------------------------------------------------------------------------
df_adjusted = (
    df_joined
      .withColumn("prev_day_flag",
          F.when(F.col("dest_FL_DATE") < F.col("FL_DATE"), 1).otherwise(0)
      )
      .withColumn("prev_ARR_TIME_MINUTES_ADJ",
          F.col("prev_ARR_TIME_MINUTES") - F.col("prev_day_flag") * 1440
      )
      .withColumn("prev_DEP_TIME_MINUTES_ADJ",
          F.col("prev_DEP_TIME_MINUTES") - F.col("prev_day_flag") * 1440
      )
)

# ----------------------------------------------------------------------------
# STEP 6: Window + rank → pick the most recent prior flight by date & time
# ----------------------------------------------------------------------------
window_spec = Window.partitionBy("orig.TAIL_NUM", "orig.ORIGIN", "orig.FL_DATE").orderBy(
    F.col("dest_FL_DATE").desc(),
    F.col("prev_ARR_TIME_MINUTES_ADJ").desc()
)
df_ranked = df_adjusted.withColumn("rn", F.row_number().over(window_spec))

# ----------------------------------------------------------------------------
# STEP 7: Compute gaps & enforce 2-hour threshold
# ----------------------------------------------------------------------------
df_full = (
    df_ranked.filter(F.col("rn")==1)
      .withColumn("TIME_BETWEEN_ARR_AND_SCHEDULED_DEP",
          F.col("CRS_DEP_TIME_MINUTES") - F.col("prev_ARR_TIME_MINUTES_ADJ")
      )
      .withColumn("TIME_SINCE_PREV_DEP",
          F.col("CRS_DEP_TIME_MINUTES") - F.col("prev_DEP_TIME_MINUTES_ADJ")
      )
      .withColumn(
          "TIME_BETWEEN_ARR_AND_SCHEDULED_DEP",
          F.when(F.col("TIME_BETWEEN_ARR_AND_SCHEDULED_DEP")>=120,
                 F.col("TIME_BETWEEN_ARR_AND_SCHEDULED_DEP")).otherwise(None)
      )
      .withColumn(
          "PREV_ARR_DELAY",
          F.when(F.col("TIME_BETWEEN_ARR_AND_SCHEDULED_DEP").isNotNull(),
                 F.col("PREV_ARR_DELAY")).otherwise(None)
      )
      .withColumn(
          "PREV_DEP_DELAY",
          F.when(F.col("TIME_SINCE_PREV_DEP")>=120,
                 F.col("prev_DEP_DELAY")).otherwise(None)
      )
      .drop(
          "rn","dest_TAIL_NUM","dest_AIRPORT","dest_FL_DATE",
          "CRS_DEP_TIME_STR","CRS_DEP_TIME_MINUTES",
          "ARR_TIME_STR","ARR_TIME_MINUTES",
          "DEP_TIME_STR","DEP_TIME_MINUTES",
          "prev_ARR_TIME_MINUTES","prev_DEP_TIME_MINUTES",
          "prev_day_flag","prev_ARR_TIME_MINUTES_ADJ","prev_DEP_TIME_MINUTES_ADJ",
          "TIME_SINCE_PREV_DEP","ORIGIN_TIMEZONE","DEST_TIMEZONE"
      )
)

# ----------------------------------------------------------------------------
# STEP 8: Final select: original + engineered features in order
# ----------------------------------------------------------------------------
original_cols = df_otpw.columns

df_final = df_full.select(
    *original_cols,
    "TIME_BETWEEN_ARR_AND_SCHEDULED_DEP",
    "PREV_DEP_DELAY",
    "PREV_ARR_DELAY"
)

# Display result
display(df_final)


path name size modificationTime dbfs:/mnt/mids-w261/HW5/ HW5/ 0 1753541230145 dbfs:/mnt/mids-w261/OTPW_12M/ OTPW_12M/ 0 1753541230145 dbfs:/mnt/mids-w261/OTPW_1D_CSV/ OTPW_1D_CSV/ 0 1753541230145 dbfs:/mnt/mids-w261/OTPW_36M/ OTPW_36M/ 0 1753541230145 dbfs:/mnt/mids-w261/OTPW_3M/ OTPW_3M/ 0 1753541230145 dbfs:/mnt/mids-w261/OTPW_3M_2015.csv OTPW_3M_2015.csv 1500620247 1741625185000 dbfs:/mnt/mids-w261/OTPW_3M_2015_delta/ OTPW_3M_2015_delta/ 0 1753541230145 dbfs:/mnt/mids-w261/OTPW_60M/ OTPW_60M/ 0 1753541230145 dbfs:/mnt/mids-w261/OTPW_60M_Backup/ OTPW_60M_Backup/ 0 1753541230145 dbfs:/mnt/mids-w261/airport-codes_csv.csv airport-codes_csv.csv 6232459 1740508595000 dbfs:/mnt/mids-w261/datasets_final_project/ datasets_final_project/ 0 1753541230145 dbfs:/mnt/mids-w261/datasets_final_project_2022/ datasets_final_project_2022/ 0 1753541230145 dbfs:/mnt/mids-w261/final_project_winter_2025/ final_project_winter_2025/ 0 1753541230145 dbfs:/mnt/mids-w261/student-groups/ student-groups/ 0 1753541230145 dbfs:/mnt/mids-w261/students-groups/ students-groups/ 0 1753541230145

QUARTER DAY_OF_MONTH DAY_OF_WEEK FL_DATE OP_UNIQUE_CARRIER OP_CARRIER_AIRLINE_ID OP_CARRIER TAIL_NUM OP_CARRIER_FL_NUM ORIGIN_AIRPORT_ID ORIGIN_AIRPORT_SEQ_ID ORIGIN_CITY_MARKET_ID ORIGIN ORIGIN_CITY_NAME ORIGIN_STATE_ABR ORIGIN_STATE_FIPS ORIGIN_STATE_NM ORIGIN_WAC DEST_AIRPORT_ID DEST_AIRPORT_SEQ_ID DEST_CITY_MARKET_ID DEST DEST_CITY_NAME DEST_STATE_ABR DEST_STATE_FIPS DEST_STATE_NM DEST_WAC CRS_DEP_TIME DEP_TIME DEP_DELAY DEP_DELAY_NEW DEP_DEL15 DEP_DELAY_GROUP DEP_TIME_BLK TAXI_OUT WHEELS_OFF WHEELS_ON TAXI_IN CRS_ARR_TIME ARR_TIME ARR_DELAY ARR_DELAY_NEW ARR_DEL15 ARR_DELAY_GROUP ARR_TIME_BLK CANCELLED CANCELLATION_CODE DIVERTED CRS_ELAPSED_TIME ACTUAL_ELAPSED_TIME AIR_TIME FLIGHTS DISTANCE DISTANCE_GROUP CARRIER_DELAY WEATHER_DELAY NAS_DELAY SECURITY_DELAY LATE_AIRCRAFT_DELAY FIRST_DEP_TIME TOTAL_ADD_GTIME LONGEST_ADD_GTIME YEAR MONTH origin_airport_name origin_station_name origin_station_id origin_iata_code origin_icao origin_type origin_region origin_station_lat origin_station_lon origin_airport_lat origin_airport_lon origin_station_dis dest_airport_name dest_station_name dest_station_id dest_iata_code dest_icao dest_type dest_region dest_station_lat dest_station_lon dest_airport_lat dest_airport_lon dest_station_dis sched_depart_date_time sched_depart_date_time_UTC four_hours_prior_depart_UTC two_hours_prior_depart_UTC STATION DATE LATITUDE LONGITUDE ELEVATION NAME REPORT_TYPE SOURCE HourlyAltimeterSetting HourlyDewPointTemperature HourlyDryBulbTemperature HourlyPrecipitation HourlyPresentWeatherType HourlyPressureChange HourlyPressureTendency HourlyRelativeHumidity HourlySkyConditions HourlySeaLevelPressure HourlyStationPressure HourlyVisibility HourlyWetBulbTemperature HourlyWindDirection HourlyWindGustSpeed HourlyWindSpeed Sunrise Sunset DailyAverageDewPointTemperature DailyAverageDryBulbTemperature DailyAverageRelativeHumidity DailyAverageSeaLevelPressure DailyAverageStationPressure DailyAverageWetBulbTemperature DailyAverageWindSpeed DailyCoolingDegreeDays DailyDepartureFromNormalAverageTemperature DailyHeatingDegreeDays DailyMaximumDryBulbTemperature DailyMinimumDryBulbTemperature DailyPeakWindDirection DailyPeakWindSpeed DailyPrecipitation DailySnowDepth DailySnowfall DailySustainedWindDirection DailySustainedWindSpeed DailyWeather MonthlyAverageRH MonthlyDaysWithGT001Precip MonthlyDaysWithGT010Precip MonthlyDaysWithGT32Temp MonthlyDaysWithGT90Temp MonthlyDaysWithLT0Temp MonthlyDaysWithLT32Temp MonthlyDepartureFromNormalAverageTemperature MonthlyDepartureFromNormalCoolingDegreeDays MonthlyDepartureFromNormalHeatingDegreeDays MonthlyDepartureFromNormalMaximumTemperature MonthlyDepartureFromNormalMinimumTemperature MonthlyDepartureFromNormalPrecipitation MonthlyDewpointTemperature MonthlyGreatestPrecip MonthlyGreatestPrecipDate MonthlyGreatestSnowDepth MonthlyGreatestSnowDepthDate MonthlyGreatestSnowfall MonthlyGreatestSnowfallDate MonthlyMaxSeaLevelPressureValue MonthlyMaxSeaLevelPressureValueDate MonthlyMaxSeaLevelPressureValueTime MonthlyMaximumTemperature MonthlyMeanTemperature MonthlyMinSeaLevelPressureValue MonthlyMinSeaLevelPressureValueDate MonthlyMinSeaLevelPressureValueTime MonthlyMinimumTemperature MonthlySeaLevelPressure MonthlyStationPressure MonthlyTotalLiquidPrecipitation MonthlyTotalSnowfall MonthlyWetBulb AWND CDSD CLDD DSNW HDSD HTDD NormalsCoolingDegreeDay NormalsHeatingDegreeDay ShortDurationEndDate005 ShortDurationEndDate010 ShortDurationEndDate015 ShortDurationEndDate020 ShortDurationEndDate030 ShortDurationEndDate045 ShortDurationEndDate060 ShortDurationEndDate080 ShortDurationEndDate100 ShortDurationEndDate120 ShortDurationEndDate150 ShortDurationEndDate180 ShortDurationPrecipitationValue005 ShortDurationPrecipitationValue010 ShortDurationPrecipitationValue015 ShortDurationPrecipitationValue020 ShortDurationPrecipitationValue030 ShortDurationPrecipitationValue045 ShortDurationPrecipitationValue060 ShortDurationPrecipitationValue080 ShortDurationPrecipitationValue100 ShortDurationPrecipitat

# RF Model that adheres to FP@ guidelines

In [0]:
# Random Forest on OTPW with Time-Based CV & Blind Test Set
from pyspark.sql.functions import col, when, to_date, log, exp
from pyspark.ml.feature import StringIndexer, OneHotEncoder, VectorAssembler
from pyspark.ml import Pipeline
from pyspark.ml.regression import RandomForestRegressor
from pyspark.ml.evaluation import RegressionEvaluator

# === Step 1: Features ===
numeric_cols = [
    "CRS_ELAPSED_TIME", "DISTANCE", "MONTH",
    "TIME_BETWEEN_ARR_AND_SCHEDULED_DEP", "PREV_DEP_DELAY", "PREV_ARR_DELAY",
    "ELEVATION", "HourlyPrecipitation"
]

# Feature engineering
otpw = df_final.withColumn("DELAY_TREND", col("PREV_ARR_DELAY") - col("PREV_DEP_DELAY"))
numeric_cols += ["DELAY_TREND"]

# Cast numerics + target
for col_name in numeric_cols + ["DEP_DELAY"]:
    otpw = otpw.withColumn(col_name, col(col_name).cast("float"))

# Log transform target (with cap/floor)
otpw = otpw.withColumn("target_delay_log", when(col("DEP_DELAY") > 180, 180).otherwise(col("DEP_DELAY")))
otpw = otpw.withColumn("target_delay_log", when(col("target_delay_log") < 1, 1).otherwise(col("target_delay_log")))
otpw = otpw.withColumn("target_delay_log", log(col("target_delay_log")))
otpw = otpw.withColumn("FL_DATE", to_date("FL_DATE"))

# Final selection
clean_df = otpw.select(numeric_cols + ["target_delay_log", "DEP_DELAY", "OP_UNIQUE_CARRIER", "FL_DATE"]).dropna()

# Split by time
train_df = clean_df.filter(col("FL_DATE") <= "2021-09-30")
test_df  = clean_df.filter(col("FL_DATE") >= "2021-10-01")

# Encoding and assembly
indexer = StringIndexer(inputCol="OP_UNIQUE_CARRIER", outputCol="carrier_index", handleInvalid="keep")
encoder = OneHotEncoder(inputCol="carrier_index", outputCol="carrier_ohe")
assembler = VectorAssembler(inputCols=numeric_cols + ["carrier_ohe"], outputCol="features")

# Random Forest model
rf = RandomForestRegressor(
    featuresCol="features", labelCol="target_delay_log",
    predictionCol="prediction", numTrees=100, maxDepth=10, seed=42
)

# Pipeline
pipeline = Pipeline(stages=[indexer, encoder, assembler, rf])

# Time-based Cross-Validation
unique_dates = [row["FL_DATE"] for row in train_df.select("FL_DATE").distinct().sort("FL_DATE").collect()]
folds = 5
window_size = len(unique_dates) // (folds + 1)
metrics = []

for i in range(folds):
    train_end = unique_dates[(i + 1) * window_size]
    test_start = unique_dates[(i + 1) * window_size]
    test_end = unique_dates[(i + 2) * window_size] if (i + 2) * window_size < len(unique_dates) else unique_dates[-1]

    train_data = train_df.filter(col("FL_DATE") < train_end)
    val_data   = train_df.filter((col("FL_DATE") >= test_start) & (col("FL_DATE") < test_end))

    model = pipeline.fit(train_data)
    preds = model.transform(val_data).withColumn("predicted_delay", exp(col("prediction")))

    r2      = RegressionEvaluator(labelCol="target_delay_log", predictionCol="prediction", metricName="r2").evaluate(preds)
    rmse    = RegressionEvaluator(labelCol="target_delay_log", predictionCol="prediction", metricName="rmse").evaluate(preds)
    log_mae = RegressionEvaluator(labelCol="target_delay_log", predictionCol="prediction", metricName="mae").evaluate(preds)
    raw_mae = RegressionEvaluator(labelCol="DEP_DELAY", predictionCol="predicted_delay", metricName="mae").evaluate(preds)

    print(f"Fold {i+1} — R²: {r2:.4f}, RMSE: {rmse:.4f}, Log MAE: {log_mae:.4f}, Raw MAE: {raw_mae:.2f}")
    metrics.append((r2, rmse, log_mae, raw_mae))

# Average CV Metrics
avg_r2 = sum(m[0] for m in metrics) / folds
avg_rmse = sum(m[1] for m in metrics) / folds
avg_log_mae = sum(m[2] for m in metrics) / folds
avg_raw_mae = sum(m[3] for m in metrics) / folds

print("\n🚀 Cross-Validated Results (Training Set):")
print(f"R²:         {avg_r2:.4f}")
print(f"RMSE (log): {avg_rmse:.4f}")
print(f"MAE  (log): {avg_log_mae:.4f}")
print(f"MAE  (min): {avg_raw_mae:.2f}")

# Final blind test evaluation
final_model = pipeline.fit(train_df)
test_preds = final_model.transform(test_df).withColumn("predicted_delay", exp(col("prediction")))

test_r2 = RegressionEvaluator(labelCol="target_delay_log", predictionCol="prediction", metricName="r2").evaluate(test_preds.withColumn("prediction", col("prediction")))
test_rmse = RegressionEvaluator(labelCol="target_delay_log", predictionCol="prediction", metricName="rmse").evaluate(test_preds)
test_log_mae = RegressionEvaluator(labelCol="target_delay_log", predictionCol="prediction", metricName="mae").evaluate(test_preds)
test_raw_mae = RegressionEvaluator(labelCol="DEP_DELAY", predictionCol="predicted_delay", metricName="mae").evaluate(test_preds)

print("\n🔒 Blind Test Set Results:")
print(f"R²:         {test_r2:.4f}")
print(f"RMSE (log): {test_rmse:.4f}")
print(f"MAE  (log): {test_log_mae:.4f}")
print(f"MAE  (min): {test_raw_mae:.2f}")


Fold 1 — R²: 0.0286, RMSE: 1.2082, Log MAE: 0.9358, Raw MAE: 11.96
Fold 2 — R²: 0.0732, RMSE: 1.2544, Log MAE: 0.8799, Raw MAE: 12.72
Fold 3 — R²: 0.0857, RMSE: 1.2395, Log MAE: 0.9127, Raw MAE: 12.20
Fold 4 — R²: 0.0109, RMSE: 1.0659, Log MAE: 0.7910, Raw MAE: 9.85
